In [1]:
import AETransformation
import AEWMVFTS
import PreProcessing
from sklearn.metrics import mean_absolute_error
import math
from pyFTS.common import Util
import datetime
import statistics
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from keras.models import Model
from keras.layers import Dense, Input
from keras import regularizers
from sklearn.preprocessing import MinMaxScaler
import pyFTS
from pyFTS.benchmarks import Measures
import statistics
from pyFTS.common.Util import persist_obj, load_obj
from pyFTS.models.multivariate import common, variable, wmvfts
from pyFTS.partitioners import Grid
from pyFTS.common import Membership

2021-09-26 08:58:04.498382: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2021-09-26 08:58:04.498484: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [38]:
df = pd.read_csv('energydata_complete.csv')
test = PreProcessing.PreProcessing(df, 'Appliances')
test.clean(['index', 'date','rv1','rv2','T9','T6','Windspeed'])
data = test.data
names = ['factor_1']

In [39]:
def sliding_window_AE(data,n_windows,train_size,dim,fs, names):
    ae_wmvfts = AEWMVFTS.AEWeightedMVFTS(n_dimensions = dim,n_part = fs,endogen_variable='Appliances',names=names)
    
    result = {
         "window": [],
         "rmse": [],
         "mape": [],
         "smape": [],
         "mae": []
    }

    order = 1
    tam = len(data)
    n_windows = 30
    windows_length = math.floor(tam / n_windows)
    for ct, ttrain, ttest in Util.sliding_window(data, windows_length, 0.75, inc=1):
        if len(ttest) > 0:
        
            data_train = ttrain.loc[:,'Appliances':'Tdewpoint']
            data_test = ttest.loc[:,'Appliances':'Tdewpoint']
        
        
            print('-' * 20)
            print(f'training window {(ct)}')
            model, ae_reduced_train = ae_wmvfts.run_train_model(data=data_train, epochs=50, n_layers=2, neuron_per_layer=[50,dim], batch=40, opt='adagrad', act='softsign')
            forecast, forecast_self, ae_reduced_test = ae_wmvfts.run_test_model(model=model, data=data_test, epochs=50, n_layers=2,
                                                           neuron_per_layer=[50,dim], batch=40, opt='adagrad', act='aoftsign')
        
        #Teste e cálculo dos erros da previsão
        #appliance_test = ttest['Appliances_t+1'].values
        
        #Teste e cálculo dos erros da previsão - valor use  é Appliances o use Appliances_t+1 --> label igual por causa do model
            print("[{0: %H:%M:%S}]".format(datetime.datetime.now()) + f" getting statistics")
            rmse = Measures.rmse(ae_reduced_test['Appliances'].values.tolist(),forecast)
            mape = Measures.mape(ae_reduced_test['Appliances'].values.tolist(),forecast)
            smape = Measures.smape(ae_reduced_test['Appliances'].values.tolist(),forecast)
        
            forecast = pd.DataFrame(forecast)
            forecast.fillna(forecast.mean(),inplace=True)
            forecast = np.array(forecast).reshape(-1)
            mae = mean_absolute_error(ae_reduced_test['Appliances'].values.tolist(), forecast)
        
        # Grafico de comparação Original x Previsto para cada janela
        #fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[15, 3])
        #ax.plot(pca_reduced_test['Appliances'], label='Original')
        #ax.plot(forecast, label='Forecast')
        #handles, labels = ax.get_legend_handles_labels()
        #lgd = ax.legend(handles, labels, loc=2, bbox_to_anchor=(1, 1))
        #plt.show()
        
            result["rmse"].append(rmse)
            result["mape"].append(mape)
            result["smape"].append(smape)
            result["mae"].append(mae)
            result["window"].append(ct)
        
            
    measures = pd.DataFrame(result)
    return measures

In [40]:
ae_wmvfts = AEWMVFTS.AEWeightedMVFTS(n_dimensions = 2,n_part = 50,endogen_variable='Appliances',names=
                                     ('factor_1','factor_2'))

In [41]:
dimensions = [2,3,4,5,6]
fuzzy_sets = [10,20,30,40,50]

final_result = {
    "dimensions": [],
    "fuzzy_sets": [],
    "rmse": [],
    "mae": [],
    "mape": [],
    "smape": []
}

n_windows = 30
train_size = 0.75

for dim in dimensions:
    names.append('factor_'+str(dim))
    print (names)
    for fs in fuzzy_sets:
        measures = sliding_window_AE(data,n_windows,train_size,dim,fs, names)
        final_result["dimensions"].append(dim)
        final_result["fuzzy_sets"].append(fs)
        
        rmse = round(statistics.mean(measures['rmse']),3)
        mape = round(statistics.mean(measures['mape']),3)
        smape = round(statistics.mean(measures['smape']),3)
        mae = round(statistics.mean(measures['mae']),3)
        
        final_result["rmse"].append(rmse)
        final_result["mape"].append(mape)
        final_result["smape"].append(smape)
        final_result["mae"].append(mae)
        
        print(f'Results: {(dim,fs,rmse,mae,mape,smape)}')
        
        
final_measures_ae = pd.DataFrame(final_result) 

print("Statistics PCA-WMVFTS (test): ")
final_measures_ae

['factor_1', 'factor_2']
--------------------
training window 0


/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
17/17 [==============================] - 1s 2ms/step - loss: 0.2371
Epoch 2/50
17/17 [==============================] - 0s 2ms/step - loss: 0.2149
Epoch 3/50
17/17 [==============================] - 0s 3ms/step - loss: 0.1952
Epoch 4/50
17/17 [==============================] - 0s 3ms/step - loss: 0.1759
Epoch 5/50
17/17 [==============================] - 0s 3ms/step - loss: 0.1576
Epoch 6/50
17/17 [==============================] - 0s 3ms/step - loss: 0.1406
Epoch 7/50
17/17 [==============================] - 0s 2ms/step - loss: 0.1249
Epoch 8/50
17/17 [==============================] - 0s 3ms/step - loss: 0.1112
Epoch 9/50
17/17 [==============================] - 0s 2ms/step - loss: 0.0994
Epoch 10/50
17/17 [==============================] - 0s 2ms/step - loss: 0.0893
Epoch 11/50
17/17 [==============================] - 0s 2ms/step - loss: 0.0809
Epoch 12/50
17/17 [==============================] - 0s 2ms/step - loss: 0.0740
Epoch 13/50
17/17 [==============================

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
6/6 [==============================] - 1s 3ms/step - loss: 0.3698
Epoch 2/50
6/6 [==============================] - 0s 2ms/step - loss: 0.3583
Epoch 3/50
6/6 [==============================] - 0s 3ms/step - loss: 0.3483
Epoch 4/50
6/6 [==============================] - 0s 3ms/step - loss: 0.3390
Epoch 5/50
6/6 [==============================] - 0s 3ms/step - loss: 0.3298
Epoch 6/50
6/6 [==============================] - 0s 3ms/step - loss: 0.3210
Epoch 7/50
6/6 [==============================] - 0s 3ms/step - loss: 0.3123
Epoch 8/50
6/6 [==============================] - 0s 3ms/step - loss: 0.3039
Epoch 9/50
6/6 [==============================] - 0s 3ms/step - loss: 0.2956
Epoch 10/50
6/6 [==============================] - 0s 3ms/step - loss: 0.2875
Epoch 11/50
6/6 [==============================] - 0s 3ms/step - loss: 0.2795
Epoch 12/50
6/6 [==============================] - 0s 2ms/step - loss: 0.2717
Epoch 13/50
6/6 [==============================] - 0s 2ms/step - loss: 0.

...

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


17/17 [==============================] - 1s 2ms/step - loss: 0.2643
Epoch 2/50
17/17 [==============================] - 0s 1ms/step - loss: 0.2094
Epoch 3/50
17/17 [==============================] - 0s 1ms/step - loss: 0.1647
Epoch 4/50
17/17 [==============================] - 0s 1ms/step - loss: 0.1278
Epoch 5/50
17/17 [==============================] - 0s 1ms/step - loss: 0.1007
Epoch 6/50
17/17 [==============================] - 0s 2ms/step - loss: 0.0830
Epoch 7/50
17/17 [==============================] - 0s 1ms/step - loss: 0.0711
Epoch 8/50
17/17 [==============================] - 0s 1ms/step - loss: 0.0629
Epoch 9/50
17/17 [==============================] - 0s 2ms/step - loss: 0.0570
Epoch 10/50
17/17 [==============================] - 0s 1ms/step - loss: 0.0526
Epoch 11/50
17/17 [==============================] - 0s 1ms/step - loss: 0.0495
Epoch 12/50
17/17 [==============================] - 0s 1ms/step - loss: 0.0470
Epoch 13/50
17/17 [==============================] - 0s 1ms/

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
6/6 [==============================] - 0s 3ms/step - loss: 0.3055
Epoch 2/50
6/6 [==============================] - 0s 1ms/step - loss: 0.2306
Epoch 3/50
6/6 [==============================] - 0s 1ms/step - loss: 0.1991
Epoch 4/50
6/6 [==============================] - 0s 1ms/step - loss: 0.1791
Epoch 5/50
6/6 [==============================] - 0s 1ms/step - loss: 0.1645
Epoch 6/50
6/6 [==============================] - 0s 2ms/step - loss: 0.1523
Epoch 7/50
6/6 [==============================] - 0s 2ms/step - loss: 0.1407
Epoch 8/50
6/6 [==============================] - 0s 1ms/step - loss: 0.1310
Epoch 9/50
6/6 [==============================] - 0s 1ms/step - loss: 0.1219
Epoch 10/50
6/6 [==============================] - 0s 1ms/step - loss: 0.1140
Epoch 11/50
6/6 [==============================] - 0s 1ms/step - loss: 0.1066
Epoch 12/50
6/6 [==============================] - 0s 1ms/step - loss: 0.1001
Epoch 13/50
6/6 [==============================] - 0s 2ms/step - loss: 0.

dimensions  fuzzy_sets    rmse     mae    mape  smape
0            2          10  15.570  20.147  12.618  4.881
1            2          20   9.453   7.004   7.549  3.739
2            2          30   4.514   2.560   2.766  1.139
3            2          40   3.935   2.478   1.841  0.789
4            2          50   1.199   1.425   0.558  0.269
5            3          10   5.729   7.605   2.869  1.171
6            3          20   1.263   1.593   0.572  0.272
7            3          30   0.323   0.974   0.121  0.056
8            3          40   0.207   0.929   0.047  0.019
9            3          50   0.217   0.948   0.060  0.026
10           4          10   1.174   1.233   0.453  0.199
11           4          20   0.598   1.112   0.299  0.122
12           4          30   0.121   0.932   0.061  0.029
13           4          40   0.043   0.913   0.024  0.009
14           4          50   0.039   0.912   0.024  0.009
15           5          10   0.484   0.980   0.043  0.019
16           5          20   0.080   0.918   0.026  0.010
17           5          30   0.047   0.914   0.024  0.009
18           5          40   0.041   0.913   0.024  0.009
19           5          50   0.039   0.912   0.024  0.009
20           6          10   0.547   0.972   0.059  0.028
21           6          20   0.070   0.917   0.025  0.009
22           6          30   0.047   0.914   0.024  0.009
23           6          40   0.041   0.913   0.024  0.009
24           6          50   0.039   0.912   0.024  0.009